In [1]:
!pip install pyabsa -U
!pip install autocuda
from pyabsa import AspectTermExtraction as ATEPC

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 724.2 kB/s eta 0:00:00
  Preparing metadata (setup.py) ... - \ | done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.9/58.9 kB 2.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 575.5/575.5 kB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 34.4/34.4 MB 37.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.2/54.2 kB 3.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 159.9/159.9 kB 9.7 MB/s eta 0:00:00
  Created wheel for seqeval: filename=seqeval-1.2.2-py3-none-any.whl size=16162 sha256=38aedc363057925c606231fea8320bd99a8c7a4994bed981db3bccc65a3e0ed6
  Stored in directory: /root/.cache/pip/wheels/1a/67/4a/ad4082dd7dfc30f2abfe4d80a2ed5926a506eb8a972b4767fa
Successfully built seqeval
  Attempting uninstall: scipy
    Found existing installation: scipy 1.11.4
    Uninstalling scipy-1.11.4:
      Successfully uninstalled scipy-1.11.4
ERROR: pip's dependency resolver

2024-06-03 20:20:54.891386: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-06-03 20:20:54.891495: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-06-03 20:20:55.065436: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [2]:
import autocuda
import random

#from metric_visualizer import MetricVisualizer
from pyabsa import AspectTermExtraction as ATEPC
# Put your dataset into integrated_datasets folder, it this folder does not exist, you need to call:
from pyabsa import download_all_available_datasets
from pyabsa import DatasetItem
from pyabsa import ModelSaveOption, DeviceTypeOption
from metric_visualizer import MetricVisualizer
import warnings
import torch
from pyabsa import __version__
assert __version__ >= '1.8.20'

from metric_visualizer import __version__
assert __version__ >= '0.4.0'


/opt/conda/lib/python3.10/multiprocessing/pool.py:268: ResourceWarning: unclosed running multiprocessing pool <multiprocessing.pool.Pool state=RUN pool_size=1>
  _warn(f"unclosed running multiprocessing pool {self!r}",


In [3]:
#device = autocuda.auto_cuda()
warnings.filterwarnings('ignore')
download_all_available_datasets()
dataset = DatasetItem(r"integrated_datasets/atepc_datasets/133.finNews")

[2024-06-03 20:21:14] (2.4.1.post1) Clone ABSADatasets from https://github.com/yangheng95/ABSADatasets.git


In [4]:
config = (
    ATEPC.ATEPCConfigManager.get_atepc_config_english()
)  # this config contains 'pretrained_bert', it is based on pretrained models
config.model = ATEPC.ATEPCModelList.FAST_LCF_ATEPC  # improved version of LCF-ATEPC

In [5]:
import random
import warnings
warnings.filterwarnings("ignore")

seeds = [random.randint(0, 10000) for _ in range(3)]
max_seq_lens = [60, 80, 100]

#config['auto_device'] = True
config.pretrained_bert = "yangheng/deberta-v3-base-absa-v1.1"
config.optimizer = "adamw"  # Optimizer class and str are both acceptable (from pytorch)
config.learning_rate = 0.00003
config.show_metric = True
config.batch_size = 32
config.patience = 2
config.log_step = 50
config.dropout = 0.5
config.seed = seeds
config.lcf = 'cdw'
config.num_epoch = 2
config.verbose = True  # If verbose == True, PyABSA will output the model structure and several processed data examples
config.notice = "This is a training example for aspect term extraction"
config.eta = -1  # Ensure eta is set to a valid value
MV = MetricVisualizer('model')
config.MV = MV

In [6]:
for max_seq_len in max_seq_lens:
    config.max_seq_len = max_seq_len  # Change the max_seq_len instead of eta
    ATEPC.ATEPCTrainer(
        config=config,
        dataset=dataset,  # train set and test set will be automatically detected
        checkpoint_save_mode=0,  # =None to avoid save model
        auto_device=DeviceTypeOption.AUTO,  # automatic choose CUDA or CPU
    )
    config.MV.next_trial()

[2024-06-03 20:21:21] (2.4.1.post1) Set Model Device: cuda:0
[2024-06-03 20:21:21] (2.4.1.post1) Device Name: Tesla T4


config.json:   0%|          | 0.00/1.03k [00:00<?, ?B/s]

2024-06-03 20:21:21,682 INFO: PyABSA version: 2.4.1.post1
2024-06-03 20:21:21,684 INFO: Transformers version: 4.39.3
2024-06-03 20:21:21,685 INFO: Torch version: 2.1.2+cuda12.1
2024-06-03 20:21:21,686 INFO: Device: Tesla T4
[2024-06-03 20:21:21] (2.4.1.post1) Try to load ['integrated_datasets/atepc_datasets/133.finNews'] dataset from local disk


tokenizer_config.json:   0%|          | 0.00/372 [00:00<?, ?B/s]

spm.model:   0%|          | 0.00/2.46M [00:00<?, ?B/s]

...

[2024-06-03 23:49:48] (2.4.1.post1) 
---------------------------- ATE Classification Report ----------------------------


[2024-06-03 23:49:48] (2.4.1.post1)
               precision    recall  f1-score   support

         ASP     0.8695    0.9142    0.8913      2448
        CLS]     0.0000    0.0000    0.0000         0
        SEP]     1.0000    1.0000    1.0000      2448

   micro avg     0.8847    0.9571    0.9195      4896
   macro avg     0.6232    0.6381    0.6304      4896
weighted avg     0.9347    0.9571    0.9456      4896

[2024-06-03 23:49:48] (2.4.1.post1) 
---------------------------- ATE Classification Report ----------------------------



Epoch:  1| loss_apc:0.2657 | loss_ate:0.0140 |:  96%|█████████▌| 294/306 [14:08<02:06, 10.51s/it,  APC_ACC: 87.30(max:87.30) | APC_F1: 87.37(max:87.37) | ATE_F1: 90.33(max:92.23)]

[2024-06-03 23:51:00] (2.4.1.post1) 
---------------------------- ATE Classification Report ----------------------------


[2024-06-03 23:51:00] (2.4.1.post1)
               precision    recall  f1-score   support

         ASP     0.8927    0.9142    0.9033      2448
        CLS]     0.0000    0.0000    0.0000         0
        SEP]     1.0000    1.0000    1.0000      2448

   micro avg     0.8960    0.9571    0.9255      4896
   macro avg     0.6309    0.6381    0.6344      4896
weighted avg     0.9464    0.9571    0.9517      4896

[2024-06-03 23:51:00] (2.4.1.post1) 
---------------------------- ATE Classification Report ----------------------------



Epoch:  1 | Smooth Loss: 0.6590: 100%|██████████| 306/306 [14:28<00:00,  2.84s/it,  APC_ACC: 87.30(max:87.30) | APC_F1: 87.37(max:87.37) | ATE_F1: 90.33(max:92.23)]


[2024-06-03 23:51:49] (2.4.1.post1) 
---------------------------- ATE Classification Report ----------------------------


[2024-06-03 23:51:49] (2.4.1.post1)
               precision    recall  f1-score   support

         ASP     0.9239    0.9330    0.9285      2448
        CLS]     0.0000    0.0000    0.0000         0
        SEP]     1.0000    1.0000    1.0000      2448

   micro avg     0.9109    0.9665    0.9379      4896
   macro avg     0.6413    0.6443    0.6428      4896
weighted avg     0.9620    0.9665    0.9642      4896

[2024-06-03 23:51:49] (2.4.1.post1) 
---------------------------- ATE Classification Report ----------------------------

2024-06-03 23:51:49,757 INFO: 
---------------------------------------------------------------------------------------------------- Raw Metric Records ----------------------------------------------------------------------------------------------------
╒════════════════════════════════╤═══════════════════════════════════════════════════

In [7]:
print(dir(MV))

['COLORS', 'COLORS_DICT', 'HATCHES', 'MARKERS', '__class__', '__delattr__', '__dict__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattribute__', '__getitem__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__le__', '__lt__', '__module__', '__ne__', '__new__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__setitem__', '__sizeof__', '__slotnames__', '__str__', '__subclasshook__', '__weakref__', '_get_processed_table_data', '_get_raw_table_data', '_rank_test_by_metric', '_rank_test_by_trial', 'a12_bar_plot', 'add_metric', 'bar_plot', 'box_plot', 'compile_tikz', 'drop', 'dump', 'fillna', 'load', 'log', 'log_metric', 'metric_rank_test_result', 'metrics', 'name', 'next_trial', 'pie_plot', 'pkg_name', 'pop', 'rank_test_by_metric', 'rank_test_by_trail', 'raw_summary', 'remove_outliers', 'scatter_plot', 'set_metric_colors', 'set_metric_names', 'set_trial_colors', 'set_trial_names', 'short_summary', 'short_to_csv', 'short_to_excel', 'short_to_html', 'sh

In [8]:
config.MV.summary(save_path=None, xticks=max_seq_lens)


---------------------------------------------------------------------------------------------------- Raw Metric Records ----------------------------------------------------------------------------------------------------
╒════════════════════════════════╤═══════════════════════════════════════════════════════════════╤════════════════════════════════════════════════════════════════╤═══════════╤══════════╤═════════╤═══════╤═══════╤═══════╕
│ Metric                         │ Trial                                                         │ Values                                                         │  Average  │  Median  │   Std   │  IQR  │  Min  │  Max  │
╞════════════════════════════════╪═══════════════════════════════════════════════════════════════╪════════════════════════════════════════════════════════════════╪═══════════╪══════════╪═════════╪═══════╪═══════╪═══════╡
│ Max-APC-Test-Acc w/o Valid Set │ fast_lcf_atepc-133.finNews-yangheng/deberta-v3-base-absa-v1.1 │ [84.48, 85.46, 8

'\n---------------------------------------------------------------------------------------------------- Raw Metric Records ----------------------------------------------------------------------------------------------------\n╒════════════════════════════════╤═══════════════════════════════════════════════════════════════╤════════════════════════════════════════════════════════════════╤═══════════╤══════════╤═════════╤═══════╤═══════╤═══════╕\n│ Metric                         │ Trial                                                         │ Values                                                         │  Average  │  Median  │   Std   │  IQR  │  Min  │  Max  │\n╞════════════════════════════════╪═══════════════════════════════════════════════════════════════╪════════════════════════════════════════════════════════════════╪═══════════╪══════════╪═════════╪═══════╪═══════╪═══════╡\n│ Max-APC-Test-Acc w/o Valid Set │ fast_lcf_atepc-133.finNews-yangheng/deberta-v3-base-absa-v1.1 │ [84.48, 85

In [9]:
'''
config.MV.summary(save_path=None, xticks=max_seq_lens)
config.MV.trajectory_plot(save_path=None, xticks=max_seq_lens)
config.MV.violin_plot(save_path=None, xticks=max_seq_lens)
config.MV.box_plot(save_path=None, xticks=max_seq_lens)

save_path = '{}_{}'.format(config.model_name, config.dataset_name)
config.MV.summary(save_path=r'/kaggle/working')
config.MV.trajectory_plot(save_path=r'/kaggle/working/trajectory_plot.jpg', xticks=max_seq_lens, xlabel=r'max_seq_len')
config.MV.violin_plot(save_path=r'/kaggle/working/violin_plot.jpg', xticks=max_seq_lens, xlabel=r'max_seq_len')
config.MV.box_plot(save_path=r'/kaggle/working/box_plot.jpg', xticks=max_seq_lens, xlabel=r'max_seq_len')
'''

"\nconfig.MV.summary(save_path=None, xticks=max_seq_lens)\nconfig.MV.trajectory_plot(save_path=None, xticks=max_seq_lens)\nconfig.MV.violin_plot(save_path=None, xticks=max_seq_lens)\nconfig.MV.box_plot(save_path=None, xticks=max_seq_lens)\n\nsave_path = '{}_{}'.format(config.model_name, config.dataset_name)\nconfig.MV.summary(save_path=r'/kaggle/working')\nconfig.MV.trajectory_plot(save_path=r'/kaggle/working/trajectory_plot.jpg', xticks=max_seq_lens, xlabel=r'max_seq_len')\nconfig.MV.violin_plot(save_path=r'/kaggle/working/violin_plot.jpg', xticks=max_seq_lens, xlabel=r'max_seq_len')\nconfig.MV.box_plot(save_path=r'/kaggle/working/box_plot.jpg', xticks=max_seq_lens, xlabel=r'max_seq_len')\n"

In [10]:
'''save_prefix = '{}_{}'.format(config.model_name, config.dataset_name)'''

"save_prefix = '{}_{}'.format(config.model_name, config.dataset_name)"

In [11]:
'''
import random
from metric_visualizer import MetricVisualizer
import numpy as np

MV = MetricVisualizer(name='ModelVisuals', trial_tag='Model')

repeat = 100  # number of repeats
metric_num = 3  # number of metrics

#  利用metric_visualizer监听实验吧并保存实验结果，随时重新绘制图像
trial_names = ['fast_lcf_atepc_01', 'fast_lcf_atepc_02']  # fake trial names
# trial_names = ['NSGA-II', 'NSGA-III', 'MOEA/D']  # fake trial names
# trial_names = ['Hyperparameter Setting 1', 'Hyperparameter Setting 2', 'Hyperparameter Setting 3']  # fake trial names

for n_trial in range(len(trial_names)):
    for r in range(repeat):  # repeat the experiments to plot violin or box figure
        metrics = [(np.random.random() + n + (1 if random.random() > 0.5 else -1)) for n in
                   range(metric_num)]  # n is metric scale factor
        for i, m in enumerate(metrics):
            # MV.add_metric(metric_name='metric{}'.format(i + 1), value=m)  # add metric by custom name and value
            MV.log_metric(trial_name=trial_names[n_trial], metric_name='metric{}'.format(i + 1),
                          value=m)  # add metric by custom name and value
    # MV.next_trial()  # next_trial() should be used with add_metric() to add metrics of different trials

# MV.remove_outliers()  # remove outliers
'''

"\nimport random\nfrom metric_visualizer import MetricVisualizer\nimport numpy as np\n\nMV = MetricVisualizer(name='ModelVisuals', trial_tag='Model')\n\nrepeat = 100  # number of repeats\nmetric_num = 3  # number of metrics\n\n#  利用metric_visualizer监听实验吧并保存实验结果，随时重新绘制图像\ntrial_names = ['fast_lcf_atepc_01', 'fast_lcf_atepc_02']  # fake trial names\n# trial_names = ['NSGA-II', 'NSGA-III', 'MOEA/D']  # fake trial names\n# trial_names = ['Hyperparameter Setting 1', 'Hyperparameter Setting 2', 'Hyperparameter Setting 3']  # fake trial names\n\nfor n_trial in range(len(trial_names)):\n    for r in range(repeat):  # repeat the experiments to plot violin or box figure\n        metrics = [(np.random.random() + n + (1 if random.random() > 0.5 else -1)) for n in\n                   range(metric_num)]  # n is metric scale factor\n        for i, m in enumerate(metrics):\n            # MV.add_metric(metric_name='metric{}'.format(i + 1), value=m)  # add metric by custom name and value\n            MV

In [12]:
'''aspect_extractor = ATEPC.AspectExtractor(
    checkpoint="fast_lcf_atepc_133.finNews_cdw_apcacc_73.61_apcf1_73.88_atef1_56.35"
)  # here I use the english checkpoint which is trained on all English datasets(including financial news) in PyABSA
'''

'aspect_extractor = ATEPC.AspectExtractor(\n    checkpoint="fast_lcf_atepc_133.finNews_cdw_apcacc_73.61_apcf1_73.88_atef1_56.35"\n)  # here I use the english checkpoint which is trained on all English datasets(including financial news) in PyABSA\n'